In [1]:
# import cv2
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import sys
sys.path.extend(["..", "../../backbone","../.."])
from backbones import DenseNet201b
from dataloader import create_dataloader
from metric import Metric,  calculate_metrics
from ievit_dpd2 import IEViT
from sklearn.metrics import roc_curve, auc
from tabulate import tabulate
from tqdm import tqdm

# from cam_generate import cam_generate
torch.cuda.empty_cache()

# Set device to GPU if available, else use CPU
# device = torch.device("cuda:0")
device = torch.device("cuda")
print(f"Current device: {torch.cuda.get_device_name(torch.cuda.current_device())}" if torch.cuda.is_available() else "Current device: CPU")

Current device: NVIDIA A100 80GB PCIe


In [2]:
# Define hyperparameters
batch_size = 16
num_epochs = 200
learning_rate = 0.000001
in_channel = 3
image_size = 384
# patch_size = 16p
patch_size = 32
num_workers = 4
embed_dim = 960
mlp_dim = 1024
dim_feedforward = 1024
num_layers = 12
num_labels = 21
thresholds = [0.5] * num_labels
num_classes = 21
dropout = 0.1
data_dir = '../../../../data/GT-main'
omit = [None]

In [3]:
# Create dataloaders (image.shape = torch.Size([batch_size, channel_no, H, W])
train_dataloader = create_dataloader(data_dir=data_dir, batch_size=batch_size, num_workers=num_workers, size=image_size, phase='train', omit = omit)
val_dataloader = create_dataloader(data_dir=data_dir, batch_size=batch_size, num_workers=num_workers, size=image_size, phase='val', omit = omit)
test_dataloader = create_dataloader(data_dir=data_dir, batch_size=batch_size, num_workers=num_workers, size=image_size, phase='test', omit = omit)

384
../../../../data/GT-main/./set1/train.csv
384
../../../../data/GT-main/./set1/val.csv
384
../../../../data/GT-main/./set1/test.csv


In [4]:
# Define model and optimizer
backbone = DenseNet201b(embed_dim, dropout)

# create an instance of IEVIT
model = IEViT(img_size= image_size, patch_size = patch_size, in_channels = in_channel, num_classes = num_classes, embed_dim = embed_dim, 
num_heads = num_workers, num_layers = num_layers, dim_feedforward = dim_feedforward, mlp_dim = mlp_dim, backbone=backbone, dropout = 0.1, device = device)
model.to(device)
num_params = sum(p.numel() for p in model.parameters())
print(num_params)

criterion = nn.BCEWithLogitsLoss()

# model = nn.DataParallel(model, device_ids=[0, 1, 2, 3])
# model.sigma = nn.Parameter(model.sigma, requires_grad=True)
# model.mean = nn.Parameter(model.mean, requires_grad=True)
params_to_optimize = [
    {"params": [param for name, param in model.named_parameters() if 'sigma' not in name and 'mean' not in name], "lr": 5e-5},
    {"params": [param for name, param in model.named_parameters() if 'sigma' in name and 'mean' in name], "lr": 100}
    # {"params": model.sigma, "lr": 5e-2},
    # {"params": model.mean, "lr": 5e-1}
]

optimizer = torch.optim.AdamW(params_to_optimize, weight_decay=1e-6)
scheduler = torch.optim.lr_scheduler.CosineAnnealingWarmRestarts(optimizer, T_0=10, T_mult=2)

/home/deependra/project/venv/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/deependra/project/venv/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=DenseNet201_Weights.IMAGENET1K_V1`. You can also use `weights=DenseNet201_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/home/deependra/project/venv/lib/python3.10/site-packages/torch/nn/modules/transformer.py:282: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but se

249104565


In [5]:
# Initialize Metric class
metric = Metric(num_classes=num_classes)
imp_w = None
loss1 = torch.tensor(0).to(device)
MS, FS = 0.91, 0.7
thresholds = None
# torch.autograd.set_detect_anomaly(True)
# create empty lists to store predicted probabilities and true labels for each epoch
test_preds_all, test_labels_all = [], []

# define the epochs at which to plot the ROC curve
roc_epochs = [5,10,20,30,40,50,60,70,80,90,100,120,140,160,180,200]

# create empty lists to store ROC data for each epoch
roc_fpr = []
roc_tpr = []
roc_auc = []
f1_arr = []
loss_arr = []
model_arr = []
max_ms = [0,0,0]

# with torch.autograd.detect_anomaly():
# Train and evaluate model
for epoch in range(num_epochs):
    print(f"Epoch {epoch+1}/{num_epochs}")
    print('-' * 10)

    # Train phase
    model.train()
    for images, labels in tqdm(train_dataloader):
        images, labels = images.to(device), labels.to(device)
        
        # Forward pass
        outputs, kld = model(images)
        
        loss1 = criterion(outputs, labels) 
        loss = loss1 + kld*0.01
        outputs = torch.sigmoid(outputs)
        # print(loss1.item(), kld.item(), loss.item())  
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward(retain_graph=True)  
        optimizer.step()
        optimizer.zero_grad()

        # Compute metrics on train set
        with torch.no_grad(): metric.update(outputs, labels)
    
     # Print metrics on train set
    ml_f1_score, map_score, auc_score, ml_map_score, ml_auc_score, ml_score, bin_auc, model_score, bin_f1_score, acc_list, spec_list, thresh = metric.compute()
    print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}, ML mAP: {ml_map_score:.4f}, ML F1: {ml_f1_score:.4f}, ML AUC: {ml_auc_score:.4f}, ML Score: {ml_score:.4f}, Bin AUC: {bin_auc:.4f}, Model Score: {model_score:.4f}, Bin F1: {bin_f1_score:.4f}")
    print(thresh)
    print(f'Accuracy list: {acc_list}')   
    print(f'Specificity list: {spec_list}') 
    # Reset Metric class for evaluation
    metric.reset()
    torch.cuda.empty_cache()

    # Evaluate model on validation set
    model.eval()
    running_loss = 0.0
    val_preds, val_labels = [], []
    with torch.no_grad():
        for images, labels in tqdm(val_dataloader):
            images, labels = images.to(device), labels.to(device)
            
            # Forward pass
            outputs, kld = model(images)
            running_loss += criterion(outputs, labels).item() + 0.01*kld
            outputs = torch.sigmoid(outputs)

            # append the predicted probabilities and true labels to lists for calculating ROC AUC score later
            val_preds += outputs.tolist()
            val_labels += labels.tolist()
            
            # Compute metrics on validation set
            metric.update(outputs, labels)

       # Print metrics on validation set
        ml_f1_score, map_score, auc_score, ml_map_score, ml_auc_score, ml_score, bin_auc, model_score, bin_f1_score,  acc_list, spec_list, thresh = metric.compute()
        print(f"Val - Epoch [{epoch+1}/{num_epochs}], Loss: {running_loss:.4f}, ML mAP: {ml_map_score:.4f}, ML F1: {ml_f1_score:.4f}, ML AUC: {ml_auc_score:.4f}, ML Score: {ml_score:.4f}, Bin AUC: {bin_auc:.4f}, Model Score: {model_score:.4f}, Bin F1: {bin_f1_score:.4f}")
        
        # Reset Metric class for next epoch
        metric.reset()
        del images
        del labels
        del outputs
        torch.cuda.empty_cache()   
    print(thresh)   
    print(f'Accuracy list: {acc_list}')   
    print(f'Specificity list: {spec_list}')
    
     # Evaluate model on test set
    running_loss = 0.0
    test_preds, test_labels = [], []
    
    with torch.no_grad():
        for images, labels in tqdm(test_dataloader):
            images, labels = images.to(device), labels.to(device)
 
            outputs, kld = model(images)
            running_loss += criterion(outputs, labels).item() + 0.01*kld
            outputs = torch.sigmoid(outputs)
            metric.update(outputs, labels)

            # append the predicted probabilities and true labels to lists for calculating ROC AUC score later
            test_preds += outputs.tolist()
            test_labels += labels.tolist()
 
        # Print metrics on test set
        ml_f1_score, map_score, auc_score, ml_map_score, ml_auc_score, ml_score, bin_auc, model_score, bin_f1_score,  acc_list, spec_list, thresh = metric.compute(thresholds = thresh)
        print(f"Test - Epoch [{epoch+1}/{num_epochs}], Loss: {running_loss:.4f}, ML mAP: {ml_map_score:.4f}, ML F1: {ml_f1_score:.4f}, ML AUC: {ml_auc_score:.4f}, ML Score: {ml_score:.4f}, Bin AUC: {bin_auc:.4f}, Model Score: {model_score:.4f}, Bin F1: {bin_f1_score:.4f}")
        
        f1_arr.append(ml_f1_score)
        model_arr.append(model_score)
        loss_arr.append(running_loss / len(test_dataloader))
        
        if model_score > MS and ml_f1_score > FS:
            torch.save(model, 'models/dpd3-god.pth')
            model_score, ml_f1_score = MS, FS
            
        f1_arr.append(ml_f1_score)
        model_arr.append(model_score)
        loss_arr.append(running_loss / len(val_dataloader))
        
        if max_ms[0] < model_score: 
            max_ms[0] = model_score
            max_ms[1] = epoch
            max_ms[2] = optimizer.param_groups[0]['lr']
            torch.save(model, 'models/dpd3-rfmid.pth')

        # append the predicted probabilities and true labels for this epoch to the lists for all epochs
        test_preds_all.append(test_preds)
        test_labels_all.append(test_labels)

        # check if the current epoch is in the list of epochs to plot ROC curve
        if epoch+1 in roc_epochs:
            # calculate ROC curve and AUC score for test set
            fpr, tpr, roc_thresholds = roc_curve(np.concatenate(test_labels_all).ravel(), np.concatenate(test_preds_all).ravel())
            roc_fpr.append(fpr)
            roc_tpr.append(tpr)
            roc_auc.append(auc(fpr, tpr))
        # Reset Metric class for next epoch
        metric.reset()
        del images
        del labels
        del outputs
        torch.cuda.empty_cache()     
        
    print(thresh)
    print(f'Accuracy list: {acc_list}')   
    print(f'Specificity list: {spec_list}') 
    print()   
    # Step the learning rate scheduler
    scheduler.step()      
    print(model.sigma.item(), model.mean.item())
print(MS, FS)

Epoch 1/200
----------


  0%|          | 0/159 [00:00<?, ?it/s]

[32, 16, 32, 16, 32, 32, 16, 16, 8, 32, 32, 16, 16, 32, 16, 16, 32, 16, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 32, 32, 16, 8, 32, 8, 16, 16, 16, 32, 8, 16, 32, 32, 32, 16, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 32, 16, 16, 16, 32, 32, 32, 32, 32, 32, 32, 16, 8, 16, 16, 32, 32, 32, 32, 16, 8, 16, 16, 8, 32, 32, 32, 32, 32, 32, 32, 32, 32, 16, 32, 16, 8, 32, 16, 32, 32, 32, 32, 32, 16, 32, 32, 16, 32, 32, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 32, 16, 32, 8, 32, 16, 16, 32, 32, 32, 16, 32, 16, 16, 32, 16, 32, 32, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 16, 32]


  1%|          | 1/159 [00:04<12:21,  4.69s/it]

[32, 16, 32, 16, 32, 32, 16, 16, 8, 32, 32, 16, 16, 32, 16, 16, 32, 16, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 32, 32, 16, 8, 32, 8, 16, 16, 16, 32, 8, 16, 32, 32, 32, 16, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 32, 16, 16, 16, 32, 32, 32, 32, 32, 32, 32, 16, 8, 16, 16, 32, 32, 32, 32, 16, 8, 16, 16, 8, 32, 32, 32, 32, 32, 32, 32, 32, 32, 16, 32, 16, 8, 32, 16, 32, 32, 32, 32, 32, 16, 32, 32, 16, 32, 32, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 32, 16, 32, 8, 32, 16, 16, 32, 32, 32, 16, 32, 16, 16, 32, 16, 32, 32, 32, 32, 32, 32, 32, 16, 32, 32, 32, 32, 16, 32]


...

[32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32]


 21%|██▏       | 34/159 [00:26<01:33,  1.34it/s]

[32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 8, 8, 8, 8, 8, 8, 8, 8, 8, 8, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32, 32]


 21%|██▏       | 34/159 [00:27<01:40,  1.24it/s]


KeyboardInterrupt: 

In [ ]:
print(MS, FS, max_ms)

0.91 0.7 [0.9129066248417644, 43, 3.8062464117898724e-05]


In [ ]:
# Evaluate the model on test set
model.eval()
test_preds, test_labels = [], []
with torch.no_grad():
    for images, labels in tqdm(test_dataloader):
        images, labels = images.to(device), labels.to(device)
            
        # Forward pass
        outputs, kld = model(images)
        outputs = torch.sigmoid(outputs)
        
        # append the predicted probabilities and true labels to lists for calculating ROC AUC score later
        test_preds += outputs.tolist()
        test_labels += labels.tolist()

test_labels = np.array(test_labels)
test_preds = np.array(test_preds)

metrics_dict = calculate_metrics(test_labels, test_preds, thresholds)

# Print the dictionary in tabular format using the tabulate library
headers = ['Label', 'Precision', 'Recall', 'F1', 'AUC']
table = []
for label in range(len(metrics_dict)):
    row = [label]
    for metric in ['Precision', 'Recall', 'F1', 'AUC']:
        value = metrics_dict[label][metric]
        row.append('{:.4f}'.format(value))
    table.append(row)

print(tabulate(table, headers=headers))

In [ ]:
print(model.sigma, model.mean)
k = len(f1_arr)
plt.figure(1)
#plt.plot(sorted(list(set(roc_epochs))), f1_arr)
plt.plot(range(1,k+1), f1_arr)
plt.xlabel("epochs")
plt.ylabel("f1_score")
plt.title('f1_score vs epochs')

plt.figure(2)
#plt.plot(sorted(list(set(roc_epochs))), loss_arr)
loss_arr_cpu = loss_arr.cpu().detach().numpy()
plt.plot(range(1, k + 1), loss_arr_cpu)
plt.xlabel("epochs")
plt.ylabel("Loss")


plt.figure(3)
#plt.plot(sorted(list(set(roc_epochs))), f1_arr)
plt.plot(range(1,k+1), model_arr)
plt.xlabel("epochs")
plt.ylabel("model_score")
plt.title('model_score vs epochs')

print(max_ms) 

In [ ]:
# plot ROC curve
fig2, ax2 = plt.subplots()
for i in range(len(roc_auc)):
    ax2.plot(roc_fpr[i], roc_tpr[i], label=f'ROC curve (epoch {roc_epochs[i]}, area = {roc_auc[i]:.2f})')
ax2.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
ax2.set_xlim([0.0, 1.0])
ax2.set_ylim([0.0, 1.05])
ax2.set_xlabel('False Positive Rate')
ax2.set_ylabel('True Positive Rate')
ax2.set_title('Receiver Operating Characteristic Curve')
# Set the properties for the legend
legend = ax2.legend(loc='lower right', bbox_to_anchor=(1.25, 0), fontsize='small', framealpha=0.8)

In [ ]:
# from sklearn.metrics import precision_recall_curve, roc_auc_score, f1_score
# from tabulate import tabulate

# model.eval()
# val_preds, val_labels = [], []
# with torch.no_grad():
#     for images, labels in tqdm(val_dataloader):
#         images, labels = images.to(device), labels.to(device)
            
#         # Forward pass
#         outputs, kld = model(images)
#         outputs = torch.sigmoid(outputs)
        
#         # append the predicted probabilities and true labels to lists for calculating ROC AUC score later
#         val_preds += outputs.tolist()
#         val_labels += labels.tolist()

# val_labels = np.array(val_labels)
# val_preds = np.array(val_preds)
# threshold = 0.5  # set your threshold value here
# thresholded_val_preds = np.where(val_preds > threshold, 1, 0)

# # Calculate the precision, recall, and AUC score for each label using scikit-learn's functions
# metrics_dict = {}
# for label in range(num_classes):
#     precision, recall, _ = precision_recall_curve(val_labels[label], thresholded_val_preds[label])
#     auc = roc_auc_score(val_labels[label], val_preds[label])
#     f1 = f1_score(val_labels[label], thresholded_val_preds[label], average='binary', zero_division=1)
#     metrics_dict[label] = {'Precision': precision, 'Recall': recall, 'F1': f1, 'AUC': auc}
    
# # Print the dictionary in tabular format using the tabulate library
# headers = ['Label', 'Precision', 'Recall', 'F1', 'AUC']
# table = []
# for label in range(num_classes):
#     row = [label]
#     for metric in ['Precision', 'Recall', 'F1', 'AUC']:
#         values = metrics_dict[label][metric]
#         if values.size > 0:
#             value_str = '{:.4f}'.format(values.mean(), values.max())
#         else:
#             value_str = '0.00'
#         row.append(value_str)
#     table.append(row)

# print(tabulate(table, headers=headers))

In [ ]:
import IPython

IPython.Application.instance().kernel.do_shutdown(True)  # Restart kernel with True flag